In [1]:
!python -V

Python 3.9.12


In [2]:
import pickle

In [3]:
import pandas as pd

In [4]:
import seaborn as sns
import matplotlib.pyplot as plt

In [5]:
from sklearn.feature_extraction import DictVectorizer
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Lasso
from sklearn.linear_model import Ridge

from sklearn.metrics import mean_squared_error

In [7]:
import mlflow

mlflow.set_tracking_uri("sqlite:///mlflow.db")
mlflow.set_experiment("nyc-taxi-experiment")

2022/05/28 15:22:50 INFO mlflow.tracking.fluent: Experiment with name 'nyc-taxi-experiment' does not exist. Creating a new experiment.


<Experiment: artifact_location='./mlruns/1', experiment_id='1', lifecycle_stage='active', name='nyc-taxi-experiment', tags={}>

In [8]:
def read_dataframe(filename):
    df = pd.read_parquet(filename)

    df['duration'] = df.lpep_dropoff_datetime - df.lpep_pickup_datetime
    df.duration = df.duration.apply(lambda td: td.total_seconds()/60)

    df = df[(df.duration >=1) & (df.duration<=60)]

    categorical = ['PULocationID', 'DOLocationID']
    numerical = ['trip_distance']
    df[categorical] = df[categorical].astype(str)
    
    return df

In [9]:
df_train = read_dataframe('../data/green_tripdata_2021-01.parquet')
df_val = read_dataframe('../data/green_tripdata_2021-02.parquet')

In [10]:
df_train['PU_DO'] = df_train['PULocationID'] + '_' + df_train['DOLocationID']
df_val['PU_DO'] = df_val['PULocationID'] + '_' + df_val['DOLocationID']

In [12]:
# categorical = ['PULocationID', 'DOLocationID']
categorical = ['PU_DO']
numerical = ['trip_distance']

dv = DictVectorizer()

train_dicts = df_train[categorical + numerical].to_dict(orient='records')
X_train = dv.fit_transform(train_dicts)

val_dicts = df_val[categorical + numerical].to_dict(orient='records')
X_val = dv.transform(val_dicts)

In [13]:
target = 'duration'
y_train = df_train[target].values
y_val = df_val[target].values

In [14]:
lr = LinearRegression()
lr.fit(X_train, y_train)

y_pred = lr.predict(X_val)

mean_squared_error(y_val, y_pred, squared=False)

7.4793657829373155

In [16]:
with open('models/lin_reg.bin', 'wb') as f_out:
    pickle.dump((dv, lr), f_out)

In [34]:
with mlflow.start_run():
    
    mlflow.set_tag("developer", "giovanni")
    mlflow.log_param("train-data-path", "../data/green_tripdata_2021-01.parquet")
    mlflow.log_param("valid-data-path", "../data/green_tripdata_2021-02.parquet")

    alpha = 0.1
    mlflow.log_param("alpha", alpha)
    
    lr = Lasso(alpha=0.001)
    lr.fit(X_train, y_train)

    y_pred = lr.predict(X_val)

    rmse = mean_squared_error(y_val, y_pred, squared=False)
    mlflow.log_metric("rmse", rmse)
    
    mlflow.log_artifact(local_path='models/lin_reg.bin', artifact_path='models_pickle')

In [18]:
lr = Ridge(alpha=10)
lr.fit(X_train, y_train)

y_pred = lr.predict(X_val)

mean_squared_error(y_val, y_pred, squared=False)

11.343250300184996

In [23]:
!pip install xgboost hyperopt

  Using cached xgboost-1.6.1-py3-none-manylinux2014_x86_64.whl (192.9 MB)
  Using cached hyperopt-0.2.7-py2.py3-none-any.whl (1.6 MB)
  Using cached py4j-0.10.9.5-py2.py3-none-any.whl (199 kB)


In [24]:
import xgboost as xgb

from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from hyperopt.pyll import scope

In [28]:
train = xgb.DMatrix(X_train, label=y_train)
valid = xgb.DMatrix(X_val, label=y_val)

In [29]:
def objective(params):
    with mlflow.start_run():
        mlflow.set_tag("model", "xgboost")
        mlflow.log_params(params)
        booster = xgb.train(
            params=params,
            dtrain=train,
            num_boost_round=1000,
            evals=[(valid, "validation")],
            early_stopping_rounds=50
        )
        y_pred = booster.predict(valid)
        rmse = mean_squared_error(y_val, y_pred, squared=False)
        mlflow.log_metric("rmse", rmse)
        
    return {'loss': rmse, 'status': STATUS_OK}

In [31]:
search_space = {
    'max_depth': scope.int(hp.quniform('max_depth', 4, 100, 1)),
    'learning_rate': hp.loguniform('learning_rate', -3, 0),
    'reg_alpha': hp.loguniform('reg_alpha', -5, -1),
    'reg_lambda': hp.loguniform('reg_lambda', -6, -1),
    'min_child_weight': hp.loguniform('min_child_weight', -1, 3),
    'objective': 'reg:linear',
    'seed': 42,
}

best_result = fmin(
    fn=objective,
    space=search_space,
    algo=tpe.suggest,
    max_evals=50,
    trials=Trials())

[15:59:01] WARNING: ../src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.                                                                                           
[0]	validation-rmse:16.15818                                                                                                                                                                                     
[1]	validation-rmse:12.75139                                                                                                                                                                                     
[2]	validation-rmse:10.49880                                                                                                                                                                                     
[3]	validation-rmse:9.05647                                                                                                                                     

[38]	validation-rmse:6.61739                                                                                                                                                                                     
[39]	validation-rmse:6.61675                                                                                                                                                                                     
[40]	validation-rmse:6.61600                                                                                                                                                                                     
[41]	validation-rmse:6.61519                                                                                                                                                                                     
[42]	validation-rmse:6.61342                                                                                                                                    

[77]	validation-rmse:6.58143                                                                                                                                                                                     
[78]	validation-rmse:6.58157                                                                                                                                                                                     
[79]	validation-rmse:6.58149                                                                                                                                                                                     
[80]	validation-rmse:6.58059                                                                                                                                                                                     
[81]	validation-rmse:6.58032                                                                                                                                    

[116]	validation-rmse:6.54641                                                                                                                                                                                    
[117]	validation-rmse:6.54569                                                                                                                                                                                    
[118]	validation-rmse:6.54539                                                                                                                                                                                    
[119]	validation-rmse:6.54524                                                                                                                                                                                    
[120]	validation-rmse:6.54468                                                                                                                                   

[155]	validation-rmse:6.52402                                                                                                                                                                                    
[156]	validation-rmse:6.52347                                                                                                                                                                                    
[157]	validation-rmse:6.52338                                                                                                                                                                                    
[158]	validation-rmse:6.52296                                                                                                                                                                                    
[159]	validation-rmse:6.52251                                                                                                                                   

...

[811]	validation-rmse:6.31192                                                                                                                                                                                    
[812]	validation-rmse:6.31192                                                                                                                                                                                    
[813]	validation-rmse:6.31185                                                                                                                                                                                    
[814]	validation-rmse:6.31185                                                                                                                                                                                    
[815]	validation-rmse:6.31185                                                                                                                                   

[850]	validation-rmse:6.30964                                                                                                                                                                                    
[851]	validation-rmse:6.30956                                                                                                                                                                                    
[852]	validation-rmse:6.30961                                                                                                                                                                                    
[853]	validation-rmse:6.30944                                                                                                                                                                                    
[854]	validation-rmse:6.30943                                                                                                                                   

[889]	validation-rmse:6.30873                                                                                                                                                                                    
[890]	validation-rmse:6.30867                                                                                                                                                                                    
[891]	validation-rmse:6.30872                                                                                                                                                                                    
[892]	validation-rmse:6.30881                                                                                                                                                                                    
[893]	validation-rmse:6.30873                                                                                                                                   

[928]	validation-rmse:6.30850                                                                                                                                                                                    
[929]	validation-rmse:6.30841                                                                                                                                                                                    
[930]	validation-rmse:6.30842                                                                                                                                                                                    
[931]	validation-rmse:6.30831                                                                                                                                                                                    
[932]	validation-rmse:6.30837                                                                                                                                   

[967]	validation-rmse:6.30707                                                                                                                                                                                    
[968]	validation-rmse:6.30746                                                                                                                                                                                    
[969]	validation-rmse:6.30747                                                                                                                                                                                    
[970]	validation-rmse:6.30781                                                                                                                                                                                    
[971]	validation-rmse:6.30795                                                                                                                                   

In [47]:
best_params = {
    'learning_rate':	0.22162207316820928,
    'max_depth':	13,
    'min_child_weight':	1.5083828239690327,
    'objective':	'reg:linear',
    'reg_alpha':	0.036349721553116984,
    'reg_lambda':	0.009805335702680957,
    'seed':	42    
}

mlflow.xgboost.autolog()

with mlflow.start_run() as run:
    booster = xgb.train(
        params=best_params,
        dtrain=train,
        num_boost_round=1000,
        evals=[(valid, "validation")],
        early_stopping_rounds=50
    )

    y_pred = booster.predict(valid)
    rmse = mean_squared_error(y_val, y_pred, squared=False)

[17:38:11] WARNING: ../src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[0]	validation-rmse:17.28502
[1]	validation-rmse:14.34208
[2]	validation-rmse:12.15433
[3]	validation-rmse:10.54971
[4]	validation-rmse:9.39098
[5]	validation-rmse:8.57393
[6]	validation-rmse:7.99518
[7]	validation-rmse:7.59024
[8]	validation-rmse:7.31127
[9]	validation-rmse:7.11317
[10]	validation-rmse:6.97444
[11]	validation-rmse:6.87409
[12]	validation-rmse:6.80133
[13]	validation-rmse:6.74871
[14]	validation-rmse:6.71003
[15]	validation-rmse:6.68129
[16]	validation-rmse:6.65802
[17]	validation-rmse:6.64100
[18]	validation-rmse:6.62782
[19]	validation-rmse:6.61774
[20]	validation-rmse:6.61117
[21]	validation-rmse:6.60584
[22]	validation-rmse:6.60152
[23]	validation-rmse:6.59726
[24]	validation-rmse:6.59231
[25]	validation-rmse:6.58957
[26]	validation-rmse:6.58764
[27]	validation-rmse:6.58474
[28]	validation-rmse:6.58212
[29]	validation-rmse:6.58035
[30]	validation-r

[273]	validation-rmse:6.40112
[274]	validation-rmse:6.40066
[275]	validation-rmse:6.40044
[276]	validation-rmse:6.40020
[277]	validation-rmse:6.39985
[278]	validation-rmse:6.39988
[279]	validation-rmse:6.39970
[280]	validation-rmse:6.39946
[281]	validation-rmse:6.39896
[282]	validation-rmse:6.39839
[283]	validation-rmse:6.39784
[284]	validation-rmse:6.39765
[285]	validation-rmse:6.39765
[286]	validation-rmse:6.39740
[287]	validation-rmse:6.39706
[288]	validation-rmse:6.39685
[289]	validation-rmse:6.39675
[290]	validation-rmse:6.39653
[291]	validation-rmse:6.39628
[292]	validation-rmse:6.39584
[293]	validation-rmse:6.39547
[294]	validation-rmse:6.39410
[295]	validation-rmse:6.39409
[296]	validation-rmse:6.39358
[297]	validation-rmse:6.39330
[298]	validation-rmse:6.39315
[299]	validation-rmse:6.39283
[300]	validation-rmse:6.39243
[301]	validation-rmse:6.39220
[302]	validation-rmse:6.39156
[303]	validation-rmse:6.39120
[304]	validation-rmse:6.39074
[305]	validation-rmse:6.39063
[306]	vali

[547]	validation-rmse:6.33352
[548]	validation-rmse:6.33365
[549]	validation-rmse:6.33357
[550]	validation-rmse:6.33331
[551]	validation-rmse:6.33325
[552]	validation-rmse:6.33305
[553]	validation-rmse:6.33276
[554]	validation-rmse:6.33271
[555]	validation-rmse:6.33251
[556]	validation-rmse:6.33212
[557]	validation-rmse:6.33192
[558]	validation-rmse:6.33169
[559]	validation-rmse:6.33149
[560]	validation-rmse:6.33127
[561]	validation-rmse:6.33111
[562]	validation-rmse:6.33117
[563]	validation-rmse:6.33119
[564]	validation-rmse:6.33124
[565]	validation-rmse:6.33110
[566]	validation-rmse:6.33083
[567]	validation-rmse:6.33053
[568]	validation-rmse:6.33067
[569]	validation-rmse:6.33061
[570]	validation-rmse:6.33062
[571]	validation-rmse:6.33070
[572]	validation-rmse:6.33067
[573]	validation-rmse:6.33069
[574]	validation-rmse:6.33075
[575]	validation-rmse:6.33062
[576]	validation-rmse:6.33053
[577]	validation-rmse:6.33035
[578]	validation-rmse:6.33033
[579]	validation-rmse:6.33035
[580]	vali

[820]	validation-rmse:6.30568
[821]	validation-rmse:6.30579
[822]	validation-rmse:6.30554
[823]	validation-rmse:6.30542
[824]	validation-rmse:6.30535
[825]	validation-rmse:6.30514
[826]	validation-rmse:6.30492
[827]	validation-rmse:6.30485
[828]	validation-rmse:6.30471
[829]	validation-rmse:6.30458
[830]	validation-rmse:6.30440
[831]	validation-rmse:6.30419
[832]	validation-rmse:6.30382
[833]	validation-rmse:6.30390
[834]	validation-rmse:6.30342
[835]	validation-rmse:6.30348
[836]	validation-rmse:6.30328
[837]	validation-rmse:6.30318
[838]	validation-rmse:6.30290
[839]	validation-rmse:6.30310
[840]	validation-rmse:6.30294
[841]	validation-rmse:6.30283
[842]	validation-rmse:6.30247
[843]	validation-rmse:6.30255
[844]	validation-rmse:6.30254
[845]	validation-rmse:6.30248
[846]	validation-rmse:6.30244
[847]	validation-rmse:6.30254
[848]	validation-rmse:6.30229
[849]	validation-rmse:6.30231
[850]	validation-rmse:6.30213
[851]	validation-rmse:6.30230
[852]	validation-rmse:6.30229
[853]	vali

2022/05/28 17:39:43 WARNING mlflow.xgboost: Failed to infer model signature: could not sample data to infer model signature: please ensure that autologging is enabled before constructing the dataset.


In [48]:
mlflow.xgboost.autolog(disable=True)

with mlflow.start_run():
    best_params = {
        'learning_rate':	0.22162207316820928,
        'max_depth':	13,
        'min_child_weight':	1.5083828239690327,
        'objective':	'reg:linear',
        'reg_alpha':	0.036349721553116984,
        'reg_lambda':	0.009805335702680957,
        'seed':	42    
    }

    mlflow.log_params(best_params)

    booster = xgb.train(
        params=best_params,
        dtrain=train,
        num_boost_round=1000,
        evals=[(valid, "validation")],
        early_stopping_rounds=50
    )
    
    y_pred = booster.predict(valid)
    rmse = mean_squared_error(y_val, y_pred, squared=False)
    mlflow.log_metric("rmse", rmse)
    
    with open("models/preprocessor.b", "wb") as f_out:
        pickle.dump(dv, f_out)
        
    mlflow.log_artifact("models/preprocessor.b", artifact_path="preprocessor")
    
    mlflow.xgboost.log_model(booster, artifact_path="models_mlflow")

[17:39:53] WARNING: ../src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[0]	validation-rmse:17.28502
[1]	validation-rmse:14.34208
[2]	validation-rmse:12.15433
[3]	validation-rmse:10.54971
[4]	validation-rmse:9.39098
[5]	validation-rmse:8.57393
[6]	validation-rmse:7.99518
[7]	validation-rmse:7.59024
[8]	validation-rmse:7.31127
[9]	validation-rmse:7.11317
[10]	validation-rmse:6.97444
[11]	validation-rmse:6.87409
[12]	validation-rmse:6.80133
[13]	validation-rmse:6.74871
[14]	validation-rmse:6.71003
[15]	validation-rmse:6.68129
[16]	validation-rmse:6.65802
[17]	validation-rmse:6.64100
[18]	validation-rmse:6.62782
[19]	validation-rmse:6.61774
[20]	validation-rmse:6.61117
[21]	validation-rmse:6.60584
[22]	validation-rmse:6.60152
[23]	validation-rmse:6.59726
[24]	validation-rmse:6.59231
[25]	validation-rmse:6.58957
[26]	validation-rmse:6.58764
[27]	validation-rmse:6.58474
[28]	validation-rmse:6.58212
[29]	validation-rmse:6.58035
[30]	validation-r

[273]	validation-rmse:6.40112
[274]	validation-rmse:6.40066
[275]	validation-rmse:6.40044
[276]	validation-rmse:6.40020
[277]	validation-rmse:6.39985
[278]	validation-rmse:6.39988
[279]	validation-rmse:6.39970
[280]	validation-rmse:6.39946
[281]	validation-rmse:6.39896
[282]	validation-rmse:6.39839
[283]	validation-rmse:6.39784
[284]	validation-rmse:6.39765
[285]	validation-rmse:6.39765
[286]	validation-rmse:6.39740
[287]	validation-rmse:6.39706
[288]	validation-rmse:6.39685
[289]	validation-rmse:6.39675
[290]	validation-rmse:6.39653
[291]	validation-rmse:6.39628
[292]	validation-rmse:6.39584
[293]	validation-rmse:6.39547
[294]	validation-rmse:6.39410
[295]	validation-rmse:6.39409
[296]	validation-rmse:6.39358
[297]	validation-rmse:6.39330
[298]	validation-rmse:6.39315
[299]	validation-rmse:6.39283
[300]	validation-rmse:6.39243
[301]	validation-rmse:6.39220
[302]	validation-rmse:6.39156
[303]	validation-rmse:6.39120
[304]	validation-rmse:6.39074
[305]	validation-rmse:6.39063
[306]	vali

[547]	validation-rmse:6.33352
[548]	validation-rmse:6.33365
[549]	validation-rmse:6.33357
[550]	validation-rmse:6.33331
[551]	validation-rmse:6.33325
[552]	validation-rmse:6.33305
[553]	validation-rmse:6.33276
[554]	validation-rmse:6.33271
[555]	validation-rmse:6.33251
[556]	validation-rmse:6.33212
[557]	validation-rmse:6.33192
[558]	validation-rmse:6.33169
[559]	validation-rmse:6.33149
[560]	validation-rmse:6.33127
[561]	validation-rmse:6.33111
[562]	validation-rmse:6.33117
[563]	validation-rmse:6.33119
[564]	validation-rmse:6.33124
[565]	validation-rmse:6.33110
[566]	validation-rmse:6.33083
[567]	validation-rmse:6.33053
[568]	validation-rmse:6.33067
[569]	validation-rmse:6.33061
[570]	validation-rmse:6.33062
[571]	validation-rmse:6.33070
[572]	validation-rmse:6.33067
[573]	validation-rmse:6.33069
[574]	validation-rmse:6.33075
[575]	validation-rmse:6.33062
[576]	validation-rmse:6.33053
[577]	validation-rmse:6.33035
[578]	validation-rmse:6.33033
[579]	validation-rmse:6.33035
[580]	vali

[821]	validation-rmse:6.30579
[822]	validation-rmse:6.30554
[823]	validation-rmse:6.30542
[824]	validation-rmse:6.30535
[825]	validation-rmse:6.30514
[826]	validation-rmse:6.30492
[827]	validation-rmse:6.30485
[828]	validation-rmse:6.30471
[829]	validation-rmse:6.30458
[830]	validation-rmse:6.30440
[831]	validation-rmse:6.30419
[832]	validation-rmse:6.30382
[833]	validation-rmse:6.30390
[834]	validation-rmse:6.30342
[835]	validation-rmse:6.30348
[836]	validation-rmse:6.30328
[837]	validation-rmse:6.30318
[838]	validation-rmse:6.30290
[839]	validation-rmse:6.30310
[840]	validation-rmse:6.30294
[841]	validation-rmse:6.30283
[842]	validation-rmse:6.30247
[843]	validation-rmse:6.30255
[844]	validation-rmse:6.30254
[845]	validation-rmse:6.30248
[846]	validation-rmse:6.30244
[847]	validation-rmse:6.30254
[848]	validation-rmse:6.30229
[849]	validation-rmse:6.30231
[850]	validation-rmse:6.30213
[851]	validation-rmse:6.30230
[852]	validation-rmse:6.30229
[853]	validation-rmse:6.30239
[854]	vali

In [49]:
logged_model = 'runs:/f16b59b20c8342aa9592fde07976af7d/models_mlflow'

# Load model as a PyFuncModel.
loaded_model = mlflow.pyfunc.load_model(logged_model)

[17:41:40] WARNING: ../src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.


In [50]:
loaded_model

mlflow.pyfunc.loaded_model:
  artifact_path: models_mlflow
  flavor: mlflow.xgboost
  run_id: f16b59b20c8342aa9592fde07976af7d

In [51]:
xgboost_model = mlflow.xgboost.load_model(logged_model)

[17:41:41] WARNING: ../src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.


In [52]:
xgboost_model

In [53]:
y_pred = xgboost_model.predict(valid)

In [54]:
y_pred[:10]

array([15.000433 ,  7.2423234, 13.46561  , 24.355412 ,  9.522373 ,
       17.138618 , 12.010164 ,  9.146234 ,  8.947216 , 19.360212 ],
      dtype=float32)